In [2]:
import numpy as np
import pandas as pd
from sklearn.decomposition import PCA
import matplotlib.pyplot as plt
import seaborn as sns
%matplotlib inline

from sklearn.model_selection import train_test_split, StratifiedKFold
from imblearn.over_sampling import RandomOverSampler, SMOTE, SMOTEN
from imblearn.under_sampling import RandomUnderSampler, EditedNearestNeighbours, ClusterCentroids
from lazypredict.Supervised import LazyClassifier
from sklearn.utils import all_estimators 
from sklearn.base import ClassifierMixin
from imblearn.under_sampling import TomekLinks
from imblearn.combine import SMOTETomek
import time

pd.set_option("display.max_rows", None)
pd.set_option("display.max_columns", None)

In [11]:
import copy
from collections import Counter

cols_cible_type = ["TurnoutTimeSeconds", "TravelTimeSeconds", "PumpSecondsOnSite"]
cols_Data = [
    ["CalYear", "HourOfCall", "Postcode_district", "Month", "DayOfWeek"],
    ["CalYear", "HourOfCall", "Postcode_district", "Month", "DayOfWeek"],
    ["CalYear", "PropertyType", "StopCode"],
]
# utilise -1 sinon crée bizarrement des Nan pour les valeurs à 0 aua lieu de mettre 0
cols_cible_bins = [
    {
        "bins": np.array([-1, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 15, 20000]) * 60,
        "labels": [1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 15, 30],
    },
    {
        "bins": np.array([-1, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 15, 20000]) * 60,
        "labels": [1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 15, 30],
    },
    {
        "bins": np.array([-1, 5, 10, 15, 30, 45, 60, 120, 180, 360, 1000000]) * 60,
        "labels": [5, 10, 15, 30, 45, 60, 120, 180, 360, 1000],
    },
]

cols_cible_bins_numbers = [4, 10, 9]

cols_cible = [
    ["TurnoutTimeSeconds_min", "TurnoutTimeSeconds_mean", "TurnoutTimeSeconds_max"],
    ["TravelTimeSeconds_min", "TravelTimeSeconds_mean", "TravelTimeSeconds_max"],
    ["PumpSecondsOnSite_min", "PumpSecondsOnSite_mean", "PumpSecondsOnSite_max"],
    # NumPumpsAttending??
]

# copie profonde, sinon la simple copie fait une copie des références des ss tableaux, et leur modif modifie l'original
cols_cible_minutes = copy.deepcopy(cols_cible)


def load_df(col_cible_type):
    df = pd.read_csv(
        f"../data/_df_ready_{col_cible_type}.csv", sep=";", low_memory=False
    )
    # Contrôle
    # display(df.head(3))
    # display(df.info())
    return df


def load_df_full(col_cible_type):
    df = pd.read_csv(
        f"../data/_df_ready_full_{col_cible_type}.csv", sep=";", low_memory=False
    )
    # Contrôle
    # display(df.head(3))
    # display(df.info())
    return df

def create_cols_cible_minutes(df, index, bins=-1):
    # Crée 3 nouvelles target pour chque min/mean/max, par tranche en minutes, pour la cible type actuelle
    for index_cible, col_cible in enumerate(cols_cible[index]):
        # bins = cols_cible_bins[index]["bins"]
        # print(bins)
        # labels = cols_cible_bins[index]["labels"]
        # print(labels)
        new_name = col_cible.replace("Seconds", "Minutes")
        print(new_name, col_cible)
        # df[new_name] = pd.cut(x=df[col_cible], bins=bins, labels=labels)
        num_bins = cols_cible_bins_numbers[index] if bins == -1 else bins
        new_bins = pd.qcut(df[col_cible], q=num_bins, precision=0)
        # 2. Afficher la répartition des observations dans chaque bin
        # 2. Modifier les labels pour qu'ils correspondent à la valeur haute de chaque intervalle
        df[new_name] = new_bins.apply(lambda x: x.right)  # Prendre la valeur haute de l'intervalle
        # 3. Afficher la répartition des observations dans chaque bin
        # bin_counts = df[new_name].value_counts().sort_index()
        # print(bin_counts)
        cols_cible_minutes[index][index_cible] = new_name
        print("cols_cible", cols_cible)
        print("cols_cible_minutes", cols_cible_minutes)
        
    display(df.head(3))
    return df

def Create_X(df_limited, index):
    print(df_limited.shape)
    # Crée X sans les target
    cols_to_remove = (
        [item for sublist in cols_cible for item in sublist]
        + cols_cible_minutes[index]
        + ["NumPumpsAttending"]
    )
    print("cols_to_remove", cols_to_remove)
    X = df_limited.drop(cols_to_remove, axis=1)
    # Ne conserve que certaines colonnes explicatives
    # Crée une liste des colonnes à conserver
    cols_to_keep = [
        col
        for col in X.columns
        if any(substring in col for substring in cols_Data[index])
    ]
    print("cols_to_keep", cols_to_keep)
    # Conserver uniquement ces colonnes
    X = X[cols_to_keep]

    display(X.head(2))
    print(X.shape)
    return X

def under_sampling(X_train, y_train):
    # Réchantillonne
    print("Resampling")
    print(len(X_train))
    start_time = time.time()
    print(y_train.value_counts())
    # sampling = RandomUnderSampler(sampling_strategy="auto", random_state=42)
    print("Smote")
    sampling = SMOTE(random_state=42)
    X_train_samp, y_train_samp = sampling.fit_resample(X_train, y_train)
    print(y_train_samp.value_counts())

    # print("EditedNearestNeighbours")
    # sampling = EditedNearestNeighbours(n_jobs=-1)
    # X_train_samp, y_train_samp = sampling.fit_resample(X_train_samp, y_train_samp)
    
    # print("ClusterCentroids")
    # sampling = ClusterCentroids(random_state=42)
    # X_train_samp, y_train_samp = sampling.fit_resample(X_train, y_train) # 35 minutes sur 3 cibles


    # print("RandomUnderSampler à 60%")
    # # Compte la taille initiale des classes avant SMOTE
    # class_counts_before_smote = Counter(y_train)
    # max_class_count_before_smote = max(class_counts_before_smote.values())
    # # Calcule 60% de la taille de la classe majoritaire initiale pour chaque classe pour appliquer le RandomUnderSampler
    # sampling_strategy = {label: int(0.60 * max_class_count_before_smote) for label in class_counts_before_smote}
    # # Appliquer RandomUnderSampler pour ajuster les classes 
    # undersampler = RandomUnderSampler(sampling_strategy=sampling_strategy, random_state=42)
    # X_train_samp, y_train_samp = undersampler.fit_resample(X_train_samp, y_train_samp)


    end_time = time.time()
    print(y_train_samp.value_counts())
    print(f"Durée de RandomUnderSampler : {end_time - start_time:.2f} secondes")
    print(len(X_train_samp))
    return X_train_samp, y_train_samp

In [47]:
# vérification de l'équilibrage des classes par cible

cols_cible_filter = [
    "TurnoutTimeSeconds_mean",
    "TravelTimeSeconds_mean",
    "PumpSecondsOnSite_mean",
]

# for index, name in enumerate(cols_cible_type):
#     df = load_df(name)
#     df = create_cols_cible_minutes(df, index, name)

#     for index_cible, col_cible in enumerate(cols_cible[index]):
#         if not (col_cible in cols_cible_filter):
#             continue
#         print("---------------------------------------------------")
#         minute_col = cols_cible_minutes[index][index_cible]
#         print(col_cible, ">>", minute_col)
#         # Vérification de l'équilibre des classes pour Target
#         print("Distribution des classes pour Target :")
#         print(df[minute_col].value_counts())

#         print("duplicated", df.duplicated().sum())

print("///////////////////////////////////////////////////////////////")

for index, name in enumerate(cols_cible_type):
    df = load_df(name)

    for index_cible, col_cible in enumerate(cols_cible[index]):
        # if not (col_cible in cols_cible_filter):
        #     continue
        print("---------------------------------------------------")
        # Vérification de l'équilibre des classes pour Target
        print("Distribution qcut pour Target :", col_cible)

        # num_bins = 5  # Nombre de bins (quantiles)
        for num_bins in range(2, 12):  # Nombre de bins (quantiles)
            y_train_bins = pd.qcut(df[col_cible], q=num_bins, precision=0)
            # 2. Afficher la répartition des observations dans chaque bin
            # 2. Modifier les labels pour qu'ils correspondent à la valeur haute de chaque intervalle
            y_train_labels = y_train_bins.apply(lambda x: x.right)  # Prendre la valeur haute de l'intervalle
            # 3. Afficher la répartition des observations dans chaque bin
            bin_counts = y_train_labels.value_counts().sort_index()
            print(bin_counts)

        # y_train_bins = pd.cut(df[col_cible], bins=num_bins, precision=0)
        # # 2. Afficher la répartition des observations dans chaque bin
        # bin_counts = y_train_bins.value_counts().sort_index()
        # print(bin_counts)

        print("duplicated", df.duplicated().sum())

///////////////////////////////////////////////////////////////
---------------------------------------------------
Distribution qcut pour Target : TurnoutTimeSeconds_min
TurnoutTimeSeconds_min
66.00      800263
1192.00    791264
Name: count, dtype: int64
TurnoutTimeSeconds_min
54.00      532265
79.00      537073
1192.00    522189
Name: count, dtype: int64
TurnoutTimeSeconds_min
48.00      414285
66.00      385978
87.00      396402
1192.00    394862
Name: count, dtype: int64
TurnoutTimeSeconds_min
43.00      327710
59.00      313535
74.00      332824
94.00      309889
1192.00    307569
Name: count, dtype: int64
TurnoutTimeSeconds_min
39.00      266015
54.00      266250
66.00      267998
79.00      269075
98.00      257215
1192.00    264974
Name: count, dtype: int64
TurnoutTimeSeconds_min
37.00      238411
51.00      232624
61.00      215107
71.00      225540
84.00      240751
103.00     219175
1192.00    219919
Name: count, dtype: int64
TurnoutTimeSeconds_min
34.00      200793
48.00   

In [4]:
cols_cible_filter = [
    "TurnoutTimeSeconds_mean",
    "TravelTimeSeconds_mean",
    "PumpSecondsOnSite_mean",
]

ignore_classifiers = [
    "CalibratedClassifierCV",
    "CalibratedClassifierCV",
    "CategoricalNB",
    "ClassifierChain",
    "ComplementNB",
    "FixedThresholdClassifier",
    "GaussianProcessClassifier",
    "GradientBoostingClassifier",
    "HistGradientBoostingClassifier",
    "LabelPropagation",
    "LabelSpreading",
    "LinearSVC",
    "LogisticRegressionCV",
    "NuSVC",
    "SVC",
]

CLASSIFIERS = [
    estimator
    for estimator in all_estimators()
    if (
        issubclass(estimator[1], ClassifierMixin)
        and (not (estimator[0] in ignore_classifiers))
    )
]

all_results = pd.DataFrame()

for index, name in enumerate(cols_cible_type):
    df = load_df(name)

    # df = df[df.CalYear > 6]
    # pd.DataFrame(pd.cut(X['Age'], bins = [0, 12, 18, 30, 50, 65, np.max(df.Age)], labels=['Kid','Adolescent','Adult-','Adult','Adult+','Senior']))
    # df['age_cat'] = pd.cut(x = df['age'], bins = [19,24,28,32,36,40], labels = ['19-24', '25-28', '29-32', '33-36', '37-40'],
    #                    include_lowest = True)
    # X = df[["PumpSecondsOnSite_min", "PumpSecondsOnSite_mean", "PumpSecondsOnSite_max", "TurnoutTimeSeconds_min", "TurnoutTimeSeconds_mean",
    #               "TurnoutTimeSeconds_max", "TravelTimeSeconds_min", "TravelTimeSeconds_mean", "TravelTimeSeconds_max", "NumPumpsAttending"]]
    # plt.boxplot([df.TurnoutTimeSeconds_min, df.TurnoutTimeSeconds_mean, df.TurnoutTimeSeconds_max])
    # plt.show()
    # plt.boxplot([df.TravelTimeSeconds_min, df.TravelTimeSeconds_mean, df.TravelTimeSeconds_max])
    # plt.show()
    # plt.figure(figsize=(5, 10))
    # plt.boxplot([df.PumpSecondsOnSite_min, df.PumpSecondsOnSite_mean, df.PumpSecondsOnSite_max])
    # plt.show()
    # Auto ML
    for year_floor in range(14, 16):  # >= 2022
        df_limited = df[df.CalYear >= year_floor]  
        # test avec différents bins
        for bins in [4, 5, 8, 10]:
            df_limited = create_cols_cible_minutes(df_limited, index, bins)
            print("-----------------------------------------------------")
            print("year", 2024 - 16 + year_floor, "bins", bins)
            print("-----------------------------------------------------")
            X = Create_X(df_limited, index)
            for index_cible, col_cible in enumerate(cols_cible[index]):
                if not (col_cible in cols_cible_filter):
                    continue
                minute_col = cols_cible_minutes[index][index_cible]
                print("/////", col_cible, ">>", minute_col)
                y = df_limited[minute_col]
                X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)
                # # Réchantillonne
                # print("TomekLinks")
                # print(len(X_train))
                # start_time = time.time()
                # tomek = TomekLinks(n_jobs=-1)
                # X_train_smote, y_train_smote = tomek.fit_resample(X_train, y_train)
                # end_time = time.time()
                # print(f"Durée de TomekLinks : {end_time - start_time:.2f} secondes")
                # print(len(X_train_smote))
                # # Réchantillonne
                # print("SMOTETomek")
                # print(len(X_train))
                # start_time = time.time()
                # smote = SMOTETomek(n_jobs=-1)
                # X_train_smote, y_train_smote = smote.fit_resample(X_train, y_train)
                # end_time = time.time()
                # print(f"Durée de SMOTETomek : {end_time - start_time:.2f} secondes")
                # print(len(X_train_smote))
                # Réchantillonne
                # X_train_samp, y_train_samp = under_sampling(X_train, y_train)
                X_train_samp, y_train_samp = X_train, y_train
                # LazyPredict
                myCLASSIFIERS = CLASSIFIERS
                print(myCLASSIFIERS)  
                # myCLASSIFIERS = myCLASSIFIERS[4:6]
                reg = LazyClassifier(
                    verbose=2,
                    ignore_warnings=False,
                    custom_metric=None,
                    classifiers=myCLASSIFIERS,
                )       
                models, predictions = reg.fit(X_train_samp, X_test, y_train_samp, y_test)
                # Ajoute le nom de la colonne
                models["Target"] = minute_col
                models["Bins"] = bins
                models["Year floor"] = 2024 - 16 + year_floor
                # Concaténe dans les résultats
                all_results = pd.concat([all_results, models], axis=0)
                display(models)
                models.to_csv(
                    f"../data/_autoML_classifier_{minute_col} {bins} {year_floor}.csv", sep=";", index=True
                )
                # break
            # break
all_results = all_results.sort_values(by=["Target", "F1 Score"], ascending=False)
all_results.to_csv(f"../data/_autoML_classifier.csv", sep=";", index=True)

# tester automl avant et après PCA et aussi gridsearch pour comparer
# save du PCA

TurnoutTimeMinutes_min TurnoutTimeSeconds_min
TurnoutTimeMinutes_min
44.00      112688
64.00      114758
83.00      106502
1192.00    110299
Name: count, dtype: int64
cols_cible [['TurnoutTimeSeconds_min', 'TurnoutTimeSeconds_mean', 'TurnoutTimeSeconds_max'], ['TravelTimeSeconds_min', 'TravelTimeSeconds_mean', 'TravelTimeSeconds_max'], ['PumpSecondsOnSite_min', 'PumpSecondsOnSite_mean', 'PumpSecondsOnSite_max']]
cols_cible_minutes [['TurnoutTimeMinutes_min', 'TurnoutTimeSeconds_mean', 'TurnoutTimeSeconds_max'], ['TravelTimeSeconds_min', 'TravelTimeSeconds_mean', 'TravelTimeSeconds_max'], ['PumpSecondsOnSite_min', 'PumpSecondsOnSite_mean', 'PumpSecondsOnSite_max']]
TurnoutTimeMinutes_mean TurnoutTimeSeconds_mean
TurnoutTimeMinutes_mean
53.00      114291
70.00      113074
89.00      108903
1192.00    107979
Name: count, dtype: int64
cols_cible [['TurnoutTimeSeconds_min', 'TurnoutTimeSeconds_mean', 'TurnoutTimeSeconds_max'], ['TravelTimeSeconds_min', 'TravelTimeSeconds_mean', 'TravelTimeS

CalYear  HourOfCall_0  HourOfCall_1  HourOfCall_2  HourOfCall_3  \
1147280       13             0             0             0             0   
1147281       13             0             0             0             0   
1147282       13             0             0             0             0   

         HourOfCall_4  PropertyType_0  PropertyType_1  PropertyType_2  \
1147280             1               0               0               0   
1147281             1               0               0               0   
1147282             1               0               0               0   

         PropertyType_3  PropertyType_4  PropertyType_5  PropertyType_6  \
1147280               1               0               1               0   
1147281               1               0               1               1   
1147282               0               0               0               0   

         PropertyType_7  PropertyType_8  Postcode_district_0  \
1147280               1               0                    0   
1147281               1               1                    0   
1147282               1               0                    0   

         Postcode_district_1  Postcode_district_2  Postcode_district_3  \
1147280                    0                    0                    0   
1147281                    0                    0                    0   
1147282                    0                    0                    0   

         Postcode_district_4  NumPumpsAttending  StopCode_0  StopCode_1  \
1147280                    1               1.00           0           0   
1147281                    1               1.00           0           0   
1147282                    1               1.00           0           0   

         StopCode_2  StopCode_3  StopCode_4  Month_0  Month_1  Month_2  \
1147280           0           1           1        0        0        0   
1147281           0           1           0        0        0        0   
1147282           0           1           1        0        0        0   

         Month_3  DayOfWeek_0  DayOfWeek_1  DayOfWeek_2  \
1147280        1            0            1            0   
1147281        1            0            1            0   
1147282        1            0            1            0   

         PumpSecondsOnSite_min  PumpSecondsOnSite_mean  PumpSecondsOnSite_max  \
1147280                2880.00                 2880.00                2880.00   
1147281                 420.00                  420.00                 420.00   
1147282                 600.00                  600.00                 600.00   

         TurnoutTimeSeconds_min  TurnoutTimeSeconds_mean  \
1147280                   48.00                    48.00   
1147281                  114.00                   114.00   
1147282                  131.00                   131.00   

         TurnoutTimeSeconds_max  TravelTimeSeconds_min  \
1147280                   48.00                 133.00   
1147281                  114.00                 136.00   
1147282                  131.00                 245.00   

         TravelTimeSeconds_mean  TravelTimeSeconds_max TurnoutTimeMinutes_min  \
1147280                  133.00                 133.00                  64.00   
1147281                  136.00                 136.00                1192.00   
1147282                  245.00                 245.00                1192.00   

        TurnoutTimeMinutes_mean TurnoutTimeMinutes_max  
1147280                   53.00                  57.00  
1147281                 1192.00                1192.00  
1147282                 1192.00                1192.00

-----------------------------------------------------
year 2021 bins 4
-----------------------------------------------------
(444247, 45)
cols_to_remove ['TurnoutTimeSeconds_min', 'TurnoutTimeSeconds_mean', 'TurnoutTimeSeconds_max', 'TravelTimeSeconds_min', 'TravelTimeSeconds_mean', 'TravelTimeSeconds_max', 'PumpSecondsOnSite_min', 'PumpSecondsOnSite_mean', 'PumpSecondsOnSite_max', 'TurnoutTimeMinutes_min', 'TurnoutTimeMinutes_mean', 'TurnoutTimeMinutes_max', 'NumPumpsAttending']
cols_to_keep ['CalYear', 'HourOfCall_0', 'HourOfCall_1', 'HourOfCall_2', 'HourOfCall_3', 'HourOfCall_4', 'Postcode_district_0', 'Postcode_district_1', 'Postcode_district_2', 'Postcode_district_3', 'Postcode_district_4', 'Month_0', 'Month_1', 'Month_2', 'Month_3', 'DayOfWeek_0', 'DayOfWeek_1', 'DayOfWeek_2']


CalYear  HourOfCall_0  HourOfCall_1  HourOfCall_2  HourOfCall_3  \
1147280       13             0             0             0             0   
1147281       13             0             0             0             0   

         HourOfCall_4  Postcode_district_0  Postcode_district_1  \
1147280             1                    0                    0   
1147281             1                    0                    0   

         Postcode_district_2  Postcode_district_3  Postcode_district_4  \
1147280                    0                    0                    1   
1147281                    0                    0                    1   

         Month_0  Month_1  Month_2  Month_3  DayOfWeek_0  DayOfWeek_1  \
1147280        0        0        0        1            0            1   
1147281        0        0        0        1            0            1   

         DayOfWeek_2  
1147280            0  
1147281            0

(444247, 18)
///// TurnoutTimeSeconds_mean >> TurnoutTimeMinutes_mean
[('AdaBoostClassifier', <class 'sklearn.ensemble._weight_boosting.AdaBoostClassifier'>), ('BaggingClassifier', <class 'sklearn.ensemble._bagging.BaggingClassifier'>), ('BernoulliNB', <class 'sklearn.naive_bayes.BernoulliNB'>), ('DecisionTreeClassifier', <class 'sklearn.tree._classes.DecisionTreeClassifier'>), ('DummyClassifier', <class 'sklearn.dummy.DummyClassifier'>), ('ExtraTreeClassifier', <class 'sklearn.tree._classes.ExtraTreeClassifier'>), ('ExtraTreesClassifier', <class 'sklearn.ensemble._forest.ExtraTreesClassifier'>), ('GaussianNB', <class 'sklearn.naive_bayes.GaussianNB'>), ('KNeighborsClassifier', <class 'sklearn.neighbors._classification.KNeighborsClassifier'>), ('LinearDiscriminantAnalysis', <class 'sklearn.discriminant_analysis.LinearDiscriminantAnalysis'>), ('LogisticRegression', <class 'sklearn.linear_model._logistic.LogisticRegression'>), ('MLPClassifier', <class 'sklearn.neural_network._multilayer_

...

 83%|████████▎ | 25/30 [08:16<02:21, 28.39s/it]

ROC AUC couldn't be calculated for RidgeClassifierCV
multi_class must be in ('ovo', 'ovr')
{'Model': 'RidgeClassifierCV', 'Accuracy': 0.1935075323290228, 'Balanced Accuracy': np.float64(0.17220776265137733), 'ROC AUC': None, 'F1 Score': 0.10213880580132043, 'Time taken': 0.452592134475708}


100%|██████████| 30/30 [08:19<00:00, 16.66s/it]

ROC AUC couldn't be calculated for SGDClassifier
multi_class must be in ('ovo', 'ovr')
{'Model': 'SGDClassifier', 'Accuracy': 0.14789139225880993, 'Balanced Accuracy': np.float64(0.1367052363024588), 'ROC AUC': None, 'F1 Score': 0.10392525879251449, 'Time taken': 2.892306089401245}
SelfTrainingClassifier model failed to execute
You must pass an estimator to SelfTrainingClassifier. Use `estimator`.
StackingClassifier model failed to execute
StackingClassifier.__init__() missing 1 required positional argument: 'estimators'
TunedThresholdClassifierCV model failed to execute
TunedThresholdClassifierCV.__init__() missing 1 required positional argument: 'estimator'
VotingClassifier model failed to execute
VotingClassifier.__init__() missing 1 required positional argument: 'estimators'


Accuracy  Balanced Accuracy ROC AUC  F1 Score  \
Model                                                                          
MLPClassifier                      0.21               0.19    None      0.12   
RandomForestClassifier             0.21               0.18    None      0.12   
ExtraTreesClassifier               0.21               0.18    None      0.12   
DecisionTreeClassifier             0.21               0.18    None      0.12   
ExtraTreeClassifier                0.21               0.18    None      0.12   
BaggingClassifier                  0.21               0.18    None      0.12   
LinearDiscriminantAnalysis         0.19               0.17    None      0.12   
LogisticRegression                 0.19               0.17    None      0.11   
RidgeClassifier                    0.19               0.17    None      0.10   
RidgeClassifierCV                  0.19               0.17    None      0.10   
QuadraticDiscriminantAnalysis      0.18               0.17    None      0.12   
NearestCentroid                    0.17               0.17    None      0.12   
BernoulliNB                        0.19               0.17    None      0.09   
AdaBoostClassifier                 0.19               0.17    None      0.08   
GaussianNB                         0.19               0.17    None      0.11   
PassiveAggressiveClassifier        0.16               0.16    None      0.12   
Perceptron                         0.16               0.14    None      0.11   
SGDClassifier                      0.15               0.14    None      0.10   
KNeighborsClassifier               0.13               0.14    None      0.11   
DummyClassifier                    0.12               0.10    None      0.03   

                               Time Taken                  Target  Bins  \
Model                                                                     
MLPClassifier                       42.66  PumpMinutesOnSite_mean    10   
RandomForestClassifier               4.24  PumpMinutesOnSite_mean    10   
ExtraTreesClassifier                 4.30  PumpMinutesOnSite_mean    10   
DecisionTreeClassifier               0.24  PumpMinutesOnSite_mean    10   
ExtraTreeClassifier                  0.16  PumpMinutesOnSite_mean    10   
BaggingClassifier                    1.06  PumpMinutesOnSite_mean    10   
LinearDiscriminantAnalysis           0.31  PumpMinutesOnSite_mean    10   
LogisticRegression                   1.09  PumpMinutesOnSite_mean    10   
RidgeClassifier                      0.18  PumpMinutesOnSite_mean    10   
RidgeClassifierCV                    0.45  PumpMinutesOnSite_mean    10   
QuadraticDiscriminantAnalysis        0.28  PumpMinutesOnSite_mean    10   
NearestCentroid                      0.23  PumpMinutesOnSite_mean    10   
BernoulliNB                          0.22  PumpMinutesOnSite_mean    10   
AdaBoostClassifier                   2.74  PumpMinutesOnSite_mean    10   
GaussianNB                           0.23  PumpMinutesOnSite_mean    10   
PassiveAggressiveClassifier          1.70  PumpMinutesOnSite_mean    10   
Perceptron                           1.56  PumpMinutesOnSite_mean    10   
SGDClassifier                        2.89  PumpMinutesOnSite_mean    10   
KNeighborsClassifier               145.69  PumpMinutesOnSite_mean    10   
DummyClassifier                      0.11  PumpMinutesOnSite_mean    10   

                               Year floor  
Model                                      
MLPClassifier                        2023  
RandomForestClassifier               2023  
ExtraTreesClassifier                 2023  
DecisionTreeClassifier               2023  
ExtraTreeClassifier                  2023  
BaggingClassifier                    2023  
LinearDiscriminantAnalysis           2023  
LogisticRegression                   2023  
RidgeClassifier                      2023  
RidgeClassifierCV                    2023  
QuadraticDiscriminantAnalysis        2023  
NearestCentroid                      2023  
Ber

In [15]:
# ------------------------------------- Lazy predict par code postal

cols_cible_filter = [
    # "TurnoutTimeSeconds_mean",
    "TravelTimeSeconds_mean",
    # "PumpSecondsOnSite_mean",
]

ignore_classifiers = [
    "CalibratedClassifierCV",
    "CalibratedClassifierCV",
    "CategoricalNB",
    "ClassifierChain",
    "ComplementNB",
    "FixedThresholdClassifier",
    "GaussianProcessClassifier",
    "GradientBoostingClassifier",
    "HistGradientBoostingClassifier",
    "LabelPropagation",
    "LabelSpreading",
    "LinearSVC",
    "LogisticRegressionCV",
    "NuSVC",
    "SVC",
]

CLASSIFIERS = [
    estimator
    for estimator in all_estimators()
    if (
        issubclass(estimator[1], ClassifierMixin)
        and (not (estimator[0] in ignore_classifiers))
    )
]

all_results = pd.DataFrame()

for index, name in enumerate(cols_cible_type):
    df = load_df_full(name)

    # df = df[df.CalYear > 6]
    # pd.DataFrame(pd.cut(X['Age'], bins = [0, 12, 18, 30, 50, 65, np.max(df.Age)], labels=['Kid','Adolescent','Adult-','Adult','Adult+','Senior']))
    # df['age_cat'] = pd.cut(x = df['age'], bins = [19,24,28,32,36,40], labels = ['19-24', '25-28', '29-32', '33-36', '37-40'],
    #                    include_lowest = True)
    # X = df[["PumpSecondsOnSite_min", "PumpSecondsOnSite_mean", "PumpSecondsOnSite_max", "TurnoutTimeSeconds_min", "TurnoutTimeSeconds_mean",
    #               "TurnoutTimeSeconds_max", "TravelTimeSeconds_min", "TravelTimeSeconds_mean", "TravelTimeSeconds_max", "NumPumpsAttending"]]
    # plt.boxplot([df.TurnoutTimeSeconds_min, df.TurnoutTimeSeconds_mean, df.TurnoutTimeSeconds_max])
    # plt.show()
    # plt.boxplot([df.TravelTimeSeconds_min, df.TravelTimeSeconds_mean, df.TravelTimeSeconds_max])
    # plt.show()
    # plt.figure(figsize=(5, 10))
    # plt.boxplot([df.PumpSecondsOnSite_min, df.PumpSecondsOnSite_mean, df.PumpSecondsOnSite_max])
    # plt.show()
    # Auto ML

    for year_floor in range(13, 16):
        df_limited = df[df.CalYear >= year_floor]  # >= 2021
        # test avec différents bins
        for bins in [4]: #[4, 5, 8, 10]:
            df_limited = create_cols_cible_minutes(df_limited, index, bins)     # TODO pourrait faire des bins par code postal
            print("-----------------------------------------------------")
            print("year", 2024 - 16 + year_floor, "bins", bins)
            print("-----------------------------------------------------")

            for index_cible, col_cible in enumerate(cols_cible[index]):
                if not (col_cible in cols_cible_filter):
                    continue
                minute_col = cols_cible_minutes[index][index_cible]
                print("/////", col_cible, ">>", minute_col)

                # boucle par CP
                # Obtenez les valeurs uniques des codes postaux
                unique_postcodes = df_limited["Postcode_district"].unique()
                # Parcours de chaque code postal
                limiter = 0
                for postcode in unique_postcodes:
                    # Limite pour test
                    limiter += 1 
                    # if limiter > 4:
                    #     break
                    # Filtre par postcode et supprime la colonne
                    df_postcode = df_limited[df_limited["Postcode_district"] == postcode]
                    df_postcode = df_postcode.drop(columns=["Postcode_district"])
                    if len(df_postcode) < 5:
                        continue
                    # Crée X et y
                    X = Create_X(df_postcode, index)
                    print("Postcode_district", postcode, X.shape)
                    # display(X.head(3))
                    y = df_postcode[minute_col]
                    X_train, X_test, y_train, y_test = train_test_split(
                        X, y, test_size=0.2, random_state=42
                    )
                    # Réchantillonne
                    # X_train_samp, y_train_samp = under_sampling(X_train, y_train)
                    X_train_samp, y_train_samp = X_train, y_train
                    # LazyPredict
                    myCLASSIFIERS = CLASSIFIERS
                    print(myCLASSIFIERS)
                    # myCLASSIFIERS = myCLASSIFIERS[4:6]
                    reg = LazyClassifier(
                        verbose=0,
                        ignore_warnings=True,
                        custom_metric=None,
                        classifiers=myCLASSIFIERS,
                    )
                    models, predictions = reg.fit(
                        X_train_samp, X_test, y_train_samp, y_test
                    )
                    # Ajoute le nom de la colonne
                    models["Target"] = minute_col
                    models["Postcode_district"] = postcode
                    models["Bins"] = bins
                    models["Year floor"] = 2024 - 16 + year_floor
                    # Concaténe dans les résultats
                    all_results = pd.concat([all_results, models], axis=0)
                    # display(models)
                    # models.to_csv(
                    #     f"../data/_autoML_classifier_{minute_col} {bins} {year_floor}.csv",
                    #     sep=";",
                    #     index=True,
                    # )
                    # break
                # break
all_results = all_results.sort_values(by=["Target", "Postcode_district", "F1 Score"], ascending=False)
all_results.to_csv(f"../data/_autoML_classifier by postcode detailled.csv", sep=";", index=True)

# Calculer les statistiques par modèle
summary_df = (
    all_results.groupby(["Target", "Bins", "Year floor", "Model"])
    .agg(
        F1_Score_Mean=("F1 Score", "mean"),
        F1_Score_Min=("F1 Score", "min"),
        F1_Score_Max=("F1 Score", "max"),
    )
    .reset_index()
)
print(summary_df)
summary_df = summary_df.sort_values(by=["Target","F1_Score_Mean"], ascending=False)

# all_results = all_results.sort_values(by=["Target", "F1 Score"], ascending=False)
summary_df.to_csv(f"../data/_autoML_classifier by postcode.csv", sep=";", index=True)

# 30 mins


TurnoutTimeMinutes_min TurnoutTimeSeconds_min
cols_cible [['TurnoutTimeSeconds_min', 'TurnoutTimeSeconds_mean', 'TurnoutTimeSeconds_max'], ['TravelTimeSeconds_min', 'TravelTimeSeconds_mean', 'TravelTimeSeconds_max'], ['PumpSecondsOnSite_min', 'PumpSecondsOnSite_mean', 'PumpSecondsOnSite_max']]
cols_cible_minutes [['TurnoutTimeMinutes_min', 'TurnoutTimeMinutes_mean', 'TurnoutTimeMinutes_max'], ['TravelTimeMinutes_min', 'TravelTimeMinutes_mean', 'TravelTimeMinutes_max'], ['PumpMinutesOnSite_min', 'PumpMinutesOnSite_mean', 'PumpMinutesOnSite_max']]
TurnoutTimeMinutes_mean TurnoutTimeSeconds_mean
cols_cible [['TurnoutTimeSeconds_min', 'TurnoutTimeSeconds_mean', 'TurnoutTimeSeconds_max'], ['TravelTimeSeconds_min', 'TravelTimeSeconds_mean', 'TravelTimeSeconds_max'], ['PumpSecondsOnSite_min', 'PumpSecondsOnSite_mean', 'PumpSecondsOnSite_max']]
cols_cible_minutes [['TurnoutTimeMinutes_min', 'TurnoutTimeMinutes_mean', 'TurnoutTimeMinutes_max'], ['TravelTimeMinutes_min', 'TravelTimeMinutes_mean'

CalYear  HourOfCall_0  HourOfCall_1  HourOfCall_2  HourOfCall_3  \
1147280       13             0             0             0             0   
1147281       13             0             0             0             0   
1147282       13             0             0             0             0   

         HourOfCall_4  PropertyType_0  PropertyType_1  PropertyType_2  \
1147280             1               0               0               0   
1147281             1               0               0               0   
1147282             1               0               0               0   

         PropertyType_3  PropertyType_4  PropertyType_5  PropertyType_6  \
1147280               1               0               1               0   
1147281               1               0               1               1   
1147282               0               0               0               0   

         PropertyType_7  PropertyType_8 Postcode_district  NumPumpsAttending  \
1147280               1               0               N10               1.00   
1147281               1               1               IG8               1.00   
1147282               1               0              RM10               1.00   

         StopCode_0  StopCode_1  StopCode_2  StopCode_3  StopCode_4  Month_0  \
1147280           0           0           0           1           1        0   
1147281           0           0           0           1           0        0   
1147282           0           0           0           1           1        0   

         Month_1  Month_2  Month_3  DayOfWeek_0  DayOfWeek_1  DayOfWeek_2  \
1147280        0        0        1            0            1            0   
1147281        0        0        1            0            1            0   
1147282        0        0        1            0            1            0   

         PumpSecondsOnSite_min  PumpSecondsOnSite_mean  PumpSecondsOnSite_max  \
1147280                2880.00                 2880.00                2880.00   
1147281                 420.00                  420.00                 420.00   
1147282                 600.00                  600.00                 600.00   

         TurnoutTimeSeconds_min  TurnoutTimeSeconds_mean  \
1147280                   48.00                    48.00   
1147281                  114.00                   114.00   
1147282                  131.00                   131.00   

         TurnoutTimeSeconds_max  TravelTimeSeconds_min  \
1147280                   48.00                 133.00   
1147281                  114.00                 136.00   
1147282                  131.00                 245.00   

         TravelTimeSeconds_mean  TravelTimeSeconds_max TurnoutTimeMinutes_min  \
1147280                  133.00                 133.00                  64.00   
1147281                  136.00                 136.00                1192.00   
1147282                  245.00                 245.00                1192.00   

        TurnoutTimeMinutes_mean TurnoutTimeMinutes_max  
1147280                   53.00                  57.00  
1147281                 1192.00                1192.00  
1147282                 1192.00                1192.00

-----------------------------------------------------
year 2021 bins 4
-----------------------------------------------------
TurnoutTimeMinutes_min TurnoutTimeSeconds_min
cols_cible [['TurnoutTimeSeconds_min', 'TurnoutTimeSeconds_mean', 'TurnoutTimeSeconds_max'], ['TravelTimeSeconds_min', 'TravelTimeSeconds_mean', 'TravelTimeSeconds_max'], ['PumpSecondsOnSite_min', 'PumpSecondsOnSite_mean', 'PumpSecondsOnSite_max']]
cols_cible_minutes [['TurnoutTimeMinutes_min', 'TurnoutTimeMinutes_mean', 'TurnoutTimeMinutes_max'], ['TravelTimeMinutes_min', 'TravelTimeMinutes_mean', 'TravelTimeMinutes_max'], ['PumpMinutesOnSite_min', 'PumpMinutesOnSite_mean', 'PumpMinutesOnSite_max']]
TurnoutTimeMinutes_mean TurnoutTimeSeconds_mean
cols_cible [['TurnoutTimeSeconds_min', 'TurnoutTimeSeconds_mean', 'TurnoutTimeSeconds_max'], ['TravelTimeSeconds_min', 'TravelTimeSeconds_mean', 'TravelTimeSeconds_max'], ['PumpSecondsOnSite_min', 'PumpSecondsOnSite_mean', 'PumpSecondsOnSite_max']]
cols_cible_minutes [['Turn

CalYear  HourOfCall_0  HourOfCall_1  HourOfCall_2  HourOfCall_3  \
1248893       14             0             0             0             0   
1248894       14             0             0             0             0   
1248895       14             0             0             0             0   

         HourOfCall_4  PropertyType_0  PropertyType_1  PropertyType_2  \
1248893             1               0               0               0   
1248894             1               1               0               0   
1248895             1               0               0               1   

         PropertyType_3  PropertyType_4  PropertyType_5  PropertyType_6  \
1248893               0               0               1               0   
1248894               0               0               0               1   
1248895               0               1               1               1   

         PropertyType_7  PropertyType_8 Postcode_district  NumPumpsAttending  \
1248893               0               1               W1U               1.00   
1248894               1               1               HA1               1.00   
1248895               1               1                E6               2.00   

         StopCode_0  StopCode_1  StopCode_2  StopCode_3  StopCode_4  Month_0  \
1248893           0           0           0           1           1        0   
1248894           0           0           0           1           0        0   
1248895           0           0           1           1           0        0   

         Month_1  Month_2  Month_3  DayOfWeek_0  DayOfWeek_1  DayOfWeek_2  \
1248893        0        0        1            0            1            1   
1248894        0        0        1            0            1            1   
1248895        0        0        1            0            1            1   

         PumpSecondsOnSite_min  PumpSecondsOnSite_mean  PumpSecondsOnSite_max  \
1248893                1080.00                 1080.00                1080.00   
1248894                 540.00                  540.00                 540.00   
1248895                 360.00                  570.00                 780.00   

         TurnoutTimeSeconds_min  TurnoutTimeSeconds_mean  \
1248893                  228.00                   228.00   
1248894                   45.00                    45.00   
1248895                   61.00                    98.50   

         TurnoutTimeSeconds_max  TravelTimeSeconds_min  \
1248893                  228.00                 335.00   
1248894                   45.00                 316.00   
1248895                  136.00                 228.00   

         TravelTimeSeconds_mean  TravelTimeSeconds_max TurnoutTimeMinutes_min  \
1248893                  335.00                 335.00                1192.00   
1248894                  316.00                 316.00                  64.00   
1248895                  234.00                 240.00                  64.00   

        TurnoutTimeMinutes_mean TurnoutTimeMinutes_max  
1248893                 1192.00                1192.00  
1248894                   53.00                  57.00  
1248895                 1192.00                1192.00

-----------------------------------------------------
year 2022 bins 4
-----------------------------------------------------
TurnoutTimeMinutes_min TurnoutTimeSeconds_min
cols_cible [['TurnoutTimeSeconds_min', 'TurnoutTimeSeconds_mean', 'TurnoutTimeSeconds_max'], ['TravelTimeSeconds_min', 'TravelTimeSeconds_mean', 'TravelTimeSeconds_max'], ['PumpSecondsOnSite_min', 'PumpSecondsOnSite_mean', 'PumpSecondsOnSite_max']]
cols_cible_minutes [['TurnoutTimeMinutes_min', 'TurnoutTimeMinutes_mean', 'TurnoutTimeMinutes_max'], ['TravelTimeMinutes_min', 'TravelTimeMinutes_mean', 'TravelTimeMinutes_max'], ['PumpMinutesOnSite_min', 'PumpMinutesOnSite_mean', 'PumpMinutesOnSite_max']]
TurnoutTimeMinutes_mean TurnoutTimeSeconds_mean
cols_cible [['TurnoutTimeSeconds_min', 'TurnoutTimeSeconds_mean', 'TurnoutTimeSeconds_max'], ['TravelTimeSeconds_min', 'TravelTimeSeconds_mean', 'TravelTimeSeconds_max'], ['PumpSecondsOnSite_min', 'PumpSecondsOnSite_mean', 'PumpSecondsOnSite_max']]
cols_cible_minutes [['Turn

...

-----------------------------------------------------
year 2021 bins 4
-----------------------------------------------------
PumpMinutesOnSite_min PumpSecondsOnSite_min
cols_cible [['TurnoutTimeSeconds_min', 'TurnoutTimeSeconds_mean', 'TurnoutTimeSeconds_max'], ['TravelTimeSeconds_min', 'TravelTimeSeconds_mean', 'TravelTimeSeconds_max'], ['PumpSecondsOnSite_min', 'PumpSecondsOnSite_mean', 'PumpSecondsOnSite_max']]
cols_cible_minutes [['TurnoutTimeMinutes_min', 'TurnoutTimeMinutes_mean', 'TurnoutTimeMinutes_max'], ['TravelTimeMinutes_min', 'TravelTimeMinutes_mean', 'TravelTimeMinutes_max'], ['PumpMinutesOnSite_min', 'PumpMinutesOnSite_mean', 'PumpMinutesOnSite_max']]
PumpMinutesOnSite_mean PumpSecondsOnSite_mean
cols_cible [['TurnoutTimeSeconds_min', 'TurnoutTimeSeconds_mean', 'TurnoutTimeSeconds_max'], ['TravelTimeSeconds_min', 'TravelTimeSeconds_mean', 'TravelTimeSeconds_max'], ['PumpSecondsOnSite_min', 'PumpSecondsOnSite_mean', 'PumpSecondsOnSite_max']]
cols_cible_minutes [['TurnoutT

CalYear  HourOfCall_0  HourOfCall_1  HourOfCall_2  HourOfCall_3  \
1248893       14             0             0             0             0   
1248894       14             0             0             0             0   
1248895       14             0             0             0             0   

         HourOfCall_4  PropertyType_0  PropertyType_1  PropertyType_2  \
1248893             1               0               0               0   
1248894             1               1               0               0   
1248895             1               0               0               1   

         PropertyType_3  PropertyType_4  PropertyType_5  PropertyType_6  \
1248893               0               0               1               0   
1248894               0               0               0               1   
1248895               0               1               1               1   

         PropertyType_7  PropertyType_8 Postcode_district  NumPumpsAttending  \
1248893               0               1               W1U               1.00   
1248894               1               1               HA1               1.00   
1248895               1               1                E6               2.00   

         StopCode_0  StopCode_1  StopCode_2  StopCode_3  StopCode_4  Month_0  \
1248893           0           0           0           1           1        0   
1248894           0           0           0           1           0        0   
1248895           0           0           1           1           0        0   

         Month_1  Month_2  Month_3  DayOfWeek_0  DayOfWeek_1  DayOfWeek_2  \
1248893        0        0        1            0            1            1   
1248894        0        0        1            0            1            1   
1248895        0        0        1            0            1            1   

         PumpSecondsOnSite_min  PumpSecondsOnSite_mean  PumpSecondsOnSite_max  \
1248893                1080.00                 1080.00                1080.00   
1248894                 540.00                  540.00                 540.00   
1248895                 360.00                  570.00                 780.00   

         TurnoutTimeSeconds_min  TurnoutTimeSeconds_mean  \
1248893                  228.00                   228.00   
1248894                   45.00                    45.00   
1248895                   61.00                    98.50   

         TurnoutTimeSeconds_max  TravelTimeSeconds_min  \
1248893                  228.00                 335.00   
1248894                   45.00                 316.00   
1248895                  136.00                 228.00   

         TravelTimeSeconds_mean  TravelTimeSeconds_max PumpMinutesOnSite_min  \
1248893                  335.00                 335.00               1080.00   
1248894                  316.00                 316.00                540.00   
1248895                  234.00                 240.00                540.00   

        PumpMinutesOnSite_mean PumpMinutesOnSite_max  
1248893                1140.00               1320.00  
1248894                 600.00                660.00  
1248895                 600.00               1320.00

-----------------------------------------------------
year 2022 bins 4
-----------------------------------------------------
PumpMinutesOnSite_min PumpSecondsOnSite_min
cols_cible [['TurnoutTimeSeconds_min', 'TurnoutTimeSeconds_mean', 'TurnoutTimeSeconds_max'], ['TravelTimeSeconds_min', 'TravelTimeSeconds_mean', 'TravelTimeSeconds_max'], ['PumpSecondsOnSite_min', 'PumpSecondsOnSite_mean', 'PumpSecondsOnSite_max']]
cols_cible_minutes [['TurnoutTimeMinutes_min', 'TurnoutTimeMinutes_mean', 'TurnoutTimeMinutes_max'], ['TravelTimeMinutes_min', 'TravelTimeMinutes_mean', 'TravelTimeMinutes_max'], ['PumpMinutesOnSite_min', 'PumpMinutesOnSite_mean', 'PumpMinutesOnSite_max']]
PumpMinutesOnSite_mean PumpSecondsOnSite_mean
cols_cible [['TurnoutTimeSeconds_min', 'TurnoutTimeSeconds_mean', 'TurnoutTimeSeconds_max'], ['TravelTimeSeconds_min', 'TravelTimeSeconds_mean', 'TravelTimeSeconds_max'], ['PumpSecondsOnSite_min', 'PumpSecondsOnSite_mean', 'PumpSecondsOnSite_max']]
cols_cible_minutes [['TurnoutT

CalYear  HourOfCall_0  HourOfCall_1  HourOfCall_2  HourOfCall_3  \
1366500       15             0             0             0             0   
1366501       15             0             0             0             0   
1366502       15             0             0             0             0   

         HourOfCall_4  PropertyType_0  PropertyType_1  PropertyType_2  \
1366500             1               1               0               0   
1366501             1               0               0               1   
1366502             1               0               0               0   

         PropertyType_3  PropertyType_4  PropertyType_5  PropertyType_6  \
1366500               0               1               0               0   
1366501               0               0               1               0   
1366502               0               0               1               1   

         PropertyType_7  PropertyType_8 Postcode_district  NumPumpsAttending  \
1366500               1               0               UB2               4.00   
1366501               0               1              SW18               1.00   
1366502               0               1               CR4               2.00   

         StopCode_0  StopCode_1  StopCode_2  StopCode_3  StopCode_4  Month_0  \
1366500           0           0           1           1           0        0   
1366501           0           0           0           1           1        0   
1366502           0           0           0           1           1        0   

         Month_1  Month_2  Month_3  DayOfWeek_0  DayOfWeek_1  DayOfWeek_2  \
1366500        0        0        1            1            0            0   
1366501        0        0        1            1            0            0   
1366502        0        0        1            1            0            0   

         PumpSecondsOnSite_min  PumpSecondsOnSite_mean  PumpSecondsOnSite_max  \
1366500                 960.00                 1950.00                2760.00   
1366501                 120.00                  120.00                 120.00   
1366502                 300.00                  330.00                 360.00   

         TurnoutTimeSeconds_min  TurnoutTimeSeconds_mean  \
1366500                    2.00                    76.50   
1366501                  114.00                   114.00   
1366502                   28.00                    85.50   

         TurnoutTimeSeconds_max  TravelTimeSeconds_min  \
1366500                  105.00                 376.00   
1366501                  114.00                  93.00   
1366502                  143.00                 336.00   

         TravelTimeSeconds_mean  TravelTimeSeconds_max PumpMinutesOnSite_min  \
1366500                  414.00                1001.00               1080.00   
1366501                   93.00                  93.00                240.00   
1366502                  366.00                 396.00                540.00   

        PumpMinutesOnSite_mean PumpMinutesOnSite_max  
1366500               45960.00              45960.00  
1366501                 300.00                360.00  
1366502                 600.00                360.00

-----------------------------------------------------
year 2023 bins 4
-----------------------------------------------------
                    Target  Bins  Year floor                          Model  \
0   TravelTimeMinutes_mean     4        2021             AdaBoostClassifier   
1   TravelTimeMinutes_mean     4        2021              BaggingClassifier   
2   TravelTimeMinutes_mean     4        2021                    BernoulliNB   
3   TravelTimeMinutes_mean     4        2021         DecisionTreeClassifier   
4   TravelTimeMinutes_mean     4        2021                DummyClassifier   
5   TravelTimeMinutes_mean     4        2021            ExtraTreeClassifier   
6   TravelTimeMinutes_mean     4        2021           ExtraTreesClassifier   
7   TravelTimeMinutes_mean     4        2021                     GaussianNB   
8   TravelTimeMinutes_mean     4        2021           KNeighborsClassifier   
9   TravelTimeMinutes_mean     4        2021     LinearDiscriminantAnalysis   
10  Tr

In [ ]:
# --------------------------------------------------- Grid Search sur KNN avec poids custom
import pandas as pd
from sklearn.model_selection import GridSearchCV, train_test_split
from sklearn.neighbors import KNeighborsClassifier
import numpy as np

from sklearn.model_selection import train_test_split, KFold, cross_validate
from sklearn.metrics import classification_report, accuracy_score, f1_score

cols_cible_filter = [
    # "TurnoutTimeSeconds_mean",
    "TravelTimeSeconds_mean",
    # "PumpSecondsOnSite_mean",
]

# Hyperparamètres à tester pour chaque modèle
param_grid = {
    "KNeighborsClassifier": {
        "n_neighbors": [15, 50, 100, 500, 1000, 2000],
        "weights": ["uniform", "distance"],
        "metric": ["euclidean", "manhattan"],
        "p": [1, 2],
    },
}

classifiers = {
    "KNeighborsClassifier": KNeighborsClassifier(),
}

results = []
crossval = KFold(n_splits=5, random_state=42, shuffle=True)

# # Concaténer les bits dans l'ordre des colonnes initiales
# def combine_binary_columns(row):
#     """
#     Combine les colonnes encodées en binaire en une seule valeur entière.
#     """
#     # Extraire les colonnes encodées correspondantes
#     binary_values = ''.join(row[["Postcode_district_0", "Postcode_district_1", "Postcode_district_2", "Postcode_district_3",
#                                  "Postcode_district_4", "Postcode_district_5", "Postcode_district_6", "Postcode_district_7",
#                                  "Postcode_district_8"]].astype(int).astype(str))
#     # print(row[["Postcode_district_0", "Postcode_district_1", "Postcode_district_2", "Postcode_district_3",
#     #                              "Postcode_district_4", "Postcode_district_5", "Postcode_district_6", "Postcode_district_7",
#     #                              "Postcode_district_8"]].astype(int).astype(str))

#     # print(binary_values)
#     binary_values += format(int(row["CalYear"]), '05b')  # Spécifie un nombre fixe de 5 bits
#     # print(binary_values)
#     binary_values += ''.join(row[["Month_0", "Month_1", "Month_2", "Month_3"	,
#                                             "DayOfWeek_0", "DayOfWeek_1", "DayOfWeek_2",
#                                             "HourOfCall_0", "HourOfCall_1", "HourOfCall_2", "HourOfCall_3", "HourOfCall_4"]].astype(int).astype(str))
#     # print(binary_values)
#     # Convertir la chaîne binaire en un entier
#     return int(binary_values, 2)

for index, name in enumerate(cols_cible_type):
    if (name == "TurnoutTimeSeconds") | (name == "PumpSecondsOnSite"):
        continue
    # df = load_df(name)
    df = pd.read_csv("../data/_df_ready_TravelTimeSeconds with Weight.csv", sep=";", low_memory=False)

    for year_floor in range(14, 15):  # >= 2022
        print("-----------------------------------------------------")
        print("year", 2024 - 16 + year_floor)
        print("-----------------------------------------------------")
        df_limited = df[df.CalYear >= year_floor]  
        df_limited = create_cols_cible_minutes(df_limited, index, 4)

        # Concaténer les colonnes binaires dans l'ordre
        # df_limited["BinaryAsInt"] = df_limited.apply(combine_binary_columns, axis=1)
        # X = df_limited["BinaryAsInt"]  # Create_X(df_limited, index)
        X = df_limited[["Weight"]]
        display(X.head(3))
        for index_cible, col_cible in enumerate(cols_cible[index]):
            if not (col_cible in cols_cible_filter):
                continue
            minute_col = cols_cible_minutes[index][index_cible]
            print(
                "--------------------------------------------------------------------------------"
            )
            print("///////////////////////////", col_cible, ">>", minute_col)
            y = df_limited[minute_col]
            X_train, X_test, y_train, y_test = train_test_split(
                X, y, test_size=0.2, random_state=42
            )
            # Réchantillonne
            # X_train_samp, y_train_samp = under_sampling(X_train, y_train)
            X_train_samp, y_train_samp = X_train, y_train

            # continue

            # Exécuter GridSearchCV pour chaque modèle
            for model_name, model in classifiers.items():
                # Controle run, car potentiellement long
                print("--------------------------------")
                print(f"GridSearchCV pour {model_name}")
                grid = GridSearchCV(
                    model,
                    param_grid[model_name],
                    scoring="f1_macro",
                    cv=crossval,
                    n_jobs=1,
                    verbose=2,
                )
                # Fit et Predict
                grid.fit(X_train_samp, y_train_samp)
                y_pred = grid.best_estimator_.predict(X_test)
                # y_pred = grid.predict(X_test)
                # Meilleur score et meilleurs hyperparamètres
                best_params = grid.best_params_
                best_score = grid.best_score_
                # affiche de suite les résultat
                print(f"Meilleurs paramètres {best_params}")
                print(f"Meilleur score {best_score}")
                # Accuracy
                accuracy = accuracy_score(y_test, y_pred)
                print(f"Accuracy : {accuracy}")
                # train et test score
                score_train = grid.score(X_train_samp, y_train_samp)
                print(f"Score train : {score_train}")
                score_test = grid.score(X_test, y_test)
                print(f"Score test : {score_test}")
                # Rapport détaillé
                detailled_report = classification_report(y_test, y_pred)
                print(f"Classification report :\n {detailled_report}")
                # Matrice de confusion
                ct = pd.crosstab(
                    y_test,
                    y_pred,
                    rownames=["Classe réelle"],
                    colnames=["Classe prédite"],
                )
                display(ct)
                # Score de validation croisée
                #             scores = cross_validate(grid, X_train, y_train, cv=crossval, scoring=['accuracy', 'precision', 'recall', 'f1'])
                #             cv_test_accuracy = f" cv_test_accuracy : {scores['test_accuracy'].mean()} (+/-{scores['test_accuracy'].std()})"
                #             cv_test_precision
                #             cv_test_recall
                #             cv_test_f1

                # {'fit_time': array([1.7602632 , 1.3521595 , 1.53327417, 1.6628437 , 1.52980328]),
                #  'score_time': array([0.10070086, 0.10009599, 0.11566949, 0.09443331, 0.09455991]),
                #  'test_accuracy': array([0.87765306, 0.87768222, 0.8774344 , 0.87757839, 0.87759297]),
                #  'test_precision': array([0.36      , 0.43243243, 0.2745098 , 0.29032258, 0.38888889]),
                #  'test_recall': array([0.00107322, 0.00190794, 0.00166965, 0.00107335, 0.00250447]),
                #  'test_f1': array([0.00214005, 0.00379912, 0.00331911, 0.00213878, 0.00497689])}

                # print("[StackingClassifier]: \n Accuracy: %0.2f (+/- %0.2f)\n" % (scores['test_accuracy'].mean(), scores['test_accuracy'].std()),
                #       "F1 score: %0.2f (+/- %0.2f)" % (scores['test_f1'].mean(), scores['test_f1'].std()))
                # >>>
                # [StackingClassifier]:
                #  Accuracy: 0.76 (+/- 0.02)
                #  F1 score: 0.62 (+/- 0.04)

                # Ajouter au tableau des résultats
                results.append(
                    {
                        "Target": minute_col,
                        "Year floor": 2024 - 16 + year_floor,
                        "Model": model_name,
                        "Best Params": best_params,
                        "Best Score": best_score,
                        "Accuracy Test": accuracy,
                        "Score Train": score_train,
                        "Score Test": score_test,
                        "Detailled_report": detailled_report,
                        "Prédiction": ct,
                    }
                )
                df_results = pd.DataFrame(results)
                df_results = df_results.sort_values(
                    by=["Target", "Score Test"], ascending=False
                )
                # df_results.to_csv(
                #     f"../data/_GridSearch_classifier.csv", sep=";", index=False
                # )

print(results)
df_results = pd.DataFrame(results)
df_results = df_results.sort_values(by=["Target", "Score Test"], ascending=False)
df_results.to_csv(f"../data/_GridSearch_knn custom.csv", sep=";", index=False)

# p = plt.figure(figsize=(18,12))
# p = sns.set_theme(style="white")
# p = models=models.sort_values(by='Model Accuracy with GridSearch',ascending=False)
# p = sns.barplot(y= 'Model', x= 'Model Accuracy with GridSearch', data= models)
# for container in p.containers:
#     p.bar_label(container,label_type = 'edge',padding = 8,size = 20,color = "black",rotation = 0,
#     bbox={"boxstyle": "round", "pad": 0.6, "facecolor": "pink", "edgecolor": "Blue", "alpha": 1})
# plt.title('COMPARE THE MODEL')
# plt.xlabel('MODEL')
# plt.ylabel('Model Accuracy')
# plt.show()

-----------------------------------------------------
year 2022
-----------------------------------------------------
TravelTimeMinutes_min TravelTimeSeconds_min
cols_cible [['TurnoutTimeSeconds_min', 'TurnoutTimeSeconds_mean', 'TurnoutTimeSeconds_max'], ['TravelTimeSeconds_min', 'TravelTimeSeconds_mean', 'TravelTimeSeconds_max'], ['PumpSecondsOnSite_min', 'PumpSecondsOnSite_mean', 'PumpSecondsOnSite_max']]
cols_cible_minutes [['TurnoutTimeMinutes_min', 'TurnoutTimeMinutes_mean', 'TurnoutTimeMinutes_max'], ['TravelTimeMinutes_min', 'TravelTimeMinutes_mean', 'TravelTimeMinutes_max'], ['PumpMinutesOnSite_min', 'PumpMinutesOnSite_mean', 'PumpMinutesOnSite_max']]
TravelTimeMinutes_mean TravelTimeSeconds_mean
cols_cible [['TurnoutTimeSeconds_min', 'TurnoutTimeSeconds_mean', 'TurnoutTimeSeconds_max'], ['TravelTimeSeconds_min', 'TravelTimeSeconds_mean', 'TravelTimeSeconds_max'], ['PumpSecondsOnSite_min', 'PumpSecondsOnSite_mean', 'PumpSecondsOnSite_max']]
cols_cible_minutes [['TurnoutTimeMinu

CalYear  HourOfCall_0  HourOfCall_1  HourOfCall_2  HourOfCall_3  \
1248893       14             0             0             0             0   
1248894       14             0             0             0             0   
1248895       14             0             0             0             0   

         HourOfCall_4  PropertyType_0  PropertyType_1  PropertyType_2  \
1248893             1               0               0               0   
1248894             1               0               0               0   
1248895             1               0               0               0   

         PropertyType_3  PropertyType_4  PropertyType_5  PropertyType_6  \
1248893               0               0               0               1   
1248894               0               0               0               1   
1248895               0               0               0               1   

         PropertyType_7  Postcode_district_0  Postcode_district_1  \
1248893               1                    0                    1   
1248894               1                    0                    1   
1248895               1                    0                    0   

         Postcode_district_2  Postcode_district_3  Postcode_district_4  \
1248893                    0                    0                    0   
1248894                    0                    0                    0   
1248895                    0                    0                    1   

         Postcode_district_5  Postcode_district_6  Postcode_district_7  \
1248893                    0                    0                    0   
1248894                    1                    1                    0   
1248895                    0                    0                    0   

         Postcode_district_8  NumPumpsAttending  StopCode_0  StopCode_1  \
1248893                    0               1.00           0           0   
1248894                    0               1.00           0           0   
1248895                    0               2.00           0           0   

         StopCode_2  StopCode_3  StopCode_4  Month_0  Month_1  Month_2  \
1248893           0           1           1        0        0        0   
1248894           0           1           0        0        0        0   
1248895           1           1           0        0        0        0   

         Month_3  DayOfWeek_0  DayOfWeek_1  DayOfWeek_2  \
1248893        1            0            1            1   
1248894        1            0            1            1   
1248895        1            0            1            1   

         PumpSecondsOnSite_min  PumpSecondsOnSite_mean  PumpSecondsOnSite_max  \
1248893                1080.00                 1080.00                1080.00   
1248894                 540.00                  540.00                 540.00   
1248895                 360.00                  570.00                 780.00   

         TurnoutTimeSeconds_min  TurnoutTimeSeconds_mean  \
1248893                  228.00                   228.00   
1248894                   45.00                    45.00   
1248895                   61.00                    98.50   

         TurnoutTimeSeconds_max  TravelTimeSeconds_min  \
1248893                  228.00                 335.00   
1248894                   45.00                 316.00   
1248895                  136.00                 228.00   

         TravelTimeSeconds_mean  TravelTimeSeconds_max  Weight  \
1248893                  335.00                 335.00  524641   
1248894                  316.00                 316.00  573793   
1248895                  234.00                 240.00   65889   

        TravelTimeMinutes_min TravelTimeMinutes_mean TravelTimeMinutes_max  
1248893               1166.00                 337.00                374.00  
1248894               1166.00                 337.00                374.00  
1248895                307.00                 252.00                272.00

Weight
1248893  524641
1248894  573793
1248895   65889

--------------------------------------------------------------------------------
/////////////////////////// TravelTimeSeconds_mean >> TravelTimeMinutes_mean
--------------------------------
GridSearchCV pour KNeighborsClassifier
Fitting 5 folds for each of 48 candidates, totalling 240 fits
[CV] END metric=euclidean, n_neighbors=15, p=1, weights=uniform; total time=   4.2s
[CV] END metric=euclidean, n_neighbors=15, p=1, weights=uniform; total time=   4.2s
[CV] END metric=euclidean, n_neighbors=15, p=1, weights=uniform; total time=   4.4s
[CV] END metric=euclidean, n_neighbors=15, p=1, weights=uniform; total time=   4.1s
[CV] END metric=euclidean, n_neighbors=15, p=1, weights=uniform; total time=   4.1s
[CV] END metric=euclidean, n_neighbors=15, p=1, weights=distance; total time=   0.4s
[CV] END metric=euclidean, n_neighbors=15, p=1, weights=distance; total time=   0.4s
[CV] END metric=euclidean, n_neighbors=15, p=1, weights=distance; total time=   0.4s
[CV] END metric=euclidean, n_neig

In [32]:
# Classifiers retenus pour optimisation, prend le top 5 de chaque cible et les entraine tous
# pour voir si au final on peut limiter à certains communs

# Pour TurnoutTimeSeconds
# KNeighborsClassifier
# DecisionTreeClassifier
# ExtraTreeClassifier
# ExtraTreesClassifier
# BaggingClassifier

# Pour TravelTimeSeconds
# MLPClassifier
# RandomForestClassifier
# BaggingClassifier
# ExtraTreesClassifier
# KNeighborsClassifier

# Pour PumpSecondsOnSite
# LinearDiscriminantAnalysis
# BaggingClassifier
# RandomForestClassifier
# ExtraTreeClassifier
# ExtraTreesClassifier

# On va effectuer un GridSearchCV pour :
# KNeighborsClassifier
# DecisionTreeClassifier
# ExtraTreeClassifier
# ExtraTreesClassifier
# BaggingClassifier
# MLPClassifier
# RandomForestClassifier
# LinearDiscriminantAnalysis

import pandas as pd
from sklearn.model_selection import GridSearchCV, train_test_split
from sklearn.pipeline import Pipeline
from sklearn.preprocessing import StandardScaler
from sklearn.neighbors import KNeighborsClassifier, RadiusNeighborsClassifier
from sklearn.tree import DecisionTreeClassifier, ExtraTreeClassifier
from sklearn.ensemble import (
    ExtraTreesClassifier,
    BaggingClassifier,
    RandomForestClassifier,
    AdaBoostClassifier,
)
from sklearn.neural_network import MLPClassifier
from sklearn.linear_model import (
    PassiveAggressiveClassifier,
    Perceptron,
    LogisticRegression,
    RidgeClassifier,
    RidgeClassifierCV,
    SGDClassifier,
)
from sklearn.naive_bayes import BernoulliNB, GaussianNB
from sklearn.discriminant_analysis import (
    LinearDiscriminantAnalysis,
    QuadraticDiscriminantAnalysis,
)
from sklearn.dummy import DummyClassifier
from sklearn.neighbors import NearestCentroid
import numpy as np

from sklearn.model_selection import GridSearchCV
from sklearn.model_selection import train_test_split, KFold, cross_validate

from sklearn.metrics import classification_report, accuracy_score, f1_score

# Hyperparamètres à tester pour chaque modèle
param_grid = {
    "KNeighborsClassifier": {
        "n_neighbors": [3, 5, 10, 15],
        "weights": ["uniform", "distance"],
        # "metric": ["euclidean", "manhattan"],
        # "p": [1, 2],
    },
    "DecisionTreeClassifier": {
        "max_depth": [None, 10, 20, 30],
        "min_samples_split": [2, 5, 10],
        "criterion": ["gini", "entropy", "log_loss"],
    },
    "ExtraTreeClassifier": {
        "max_depth": [None, 10, 20, 30],
        "min_samples_split": [2, 5, 10],
        "criterion": ["gini", "entropy", "log_loss"],
    },
    # "ExtraTreesClassifier": {
    #     "n_estimators": [50, 100, 200],
    #     "max_depth": [None, 10, 20, 30],
    #     "criterion": ["gini", "entropy", "log_loss"],
    # },
    "ExtraTreesClassifier": {
        "n_estimators": [50, 100, 200],
        "max_depth": [None, 10, 20, 30],
        "criterion": ["gini", "entropy"],
    },
    "BaggingClassifier": {
        "n_estimators": [10, 50, 100],
        "max_samples": [0.5, 0.75, 1.0],
        "bootstrap": [True, False],
    },
    # "RandomForestClassifier": {
    #     "n_estimators": [10, 50, 100, 200],
    #     "max_depth": [None, 10, 20, 30],
    #     "criterion": ["gini", "entropy"],
    # },
    "RandomForestClassifier": {
        "n_estimators": [10, 50, 100, 200],
        "max_depth": [10, 20, 30],
        "criterion": ["gini", "entropy"],
    },
    "RadiusNeighborsClassifier": {
        "radius": [0.5, 1.0, 2.0],
        "weights": ["uniform", "distance"],
    },
    # "MLPClassifier": {
    #     "hidden_layer_sizes": [(50,), (100,), (50, 50), (100, 100)],
    #     "activation": ["relu", "tanh", "logistic"],
    #     "learning_rate_init": [0.001, 0.01, 0.1],
    # },
    "MLPClassifier": {
        "hidden_layer_sizes": [(100,), (50, 50), (100, 100)],
        "activation": ["relu", "tanh"],
        "learning_rate_init": [0.001, 0.01, 0.1],
    },
    "PassiveAggressiveClassifier": {
        "C": [0.1, 1.0, 10.0],
        "max_iter": [1000, 2000],
    },
    "Perceptron": {
        "penalty": [None, "l2", "l1", "elasticnet"],
        "alpha": [0.0001, 0.001, 0.01],
    },
    "AdaBoostClassifier": {
        "n_estimators": [50, 100, 200],
        "learning_rate": [0.1, 0.5, 1.0],
    },
    "LogisticRegression": {
        "penalty": ["l1", "l2", "elasticnet", "none"],
        "C": [0.1, 1.0, 10.0],
        "solver": ["liblinear", "saga"],
    },
    "LinearDiscriminantAnalysis": {
        "solver": ["svd", "lsqr", "eigen"],
        "shrinkage": [None, "auto"],
    },
    "RidgeClassifier": {
        "alpha": [0.1, 1.0, 10.0, 100.0],
    },
    "RidgeClassifierCV": {},
    "BernoulliNB": {
        "alpha": [0.01, 0.1, 1.0],
    },
    "SGDClassifier": {
        "alpha": [0.0001, 0.001, 0.01],
        "penalty": ["l2", "l1", "elasticnet"],
        "max_iter": [1000, 2000],
        "loss": ["hinge", "log"],
    },
    "QuadraticDiscriminantAnalysis": {
        "reg_param": [0.0, 0.1, 0.5],
    },
    "NearestCentroid": {},
    "GaussianNB": {},
}

classifiers = {
    # "KNeighborsClassifier": KNeighborsClassifier(),
    "DecisionTreeClassifier": DecisionTreeClassifier(),
    # "ExtraTreeClassifier": ExtraTreeClassifier(),
    "ExtraTreesClassifier": ExtraTreesClassifier(),
    "BaggingClassifier": BaggingClassifier(),
    "RandomForestClassifier": RandomForestClassifier(),
    # "RadiusNeighborsClassifier": RadiusNeighborsClassifier(),
    "MLPClassifier": MLPClassifier(),
    # "PassiveAggressiveClassifier": PassiveAggressiveClassifier(),
    # "Perceptron": Perceptron(),
    # "AdaBoostClassifier": AdaBoostClassifier(),
    # "LogisticRegression": LogisticRegression(),
    # "LinearDiscriminantAnalysis": LinearDiscriminantAnalysis(),
    # "RidgeClassifier": RidgeClassifier(),
    # "BernoulliNB": BernoulliNB(),
    # "SGDClassifier": SGDClassifier(),
    # "QuadraticDiscriminantAnalysis": QuadraticDiscriminantAnalysis(),
    # "NearestCentroid": NearestCentroid(),
    # "GaussianNB": GaussianNB(),
}

cols_cible_filter = [
    "TurnoutTimeSeconds_mean",
    "TravelTimeSeconds_mean",
    "PumpSecondsOnSite_mean",
]

results = []
crossval = KFold(n_splits=5, random_state=42, shuffle=True)

for index, name in enumerate(cols_cible_type):
    df = load_df(name)

    for year_floor in range(14, 15):  # >= 2022
        print("-----------------------------------------------------")
        print("year", 2024 - 16 + year_floor)
        print("-----------------------------------------------------")
        df_limited = df[df.CalYear >= year_floor]  
        df_limited = create_cols_cible_minutes(df_limited, index, 4)
        X = Create_X(df_limited, index)
        for index_cible, col_cible in enumerate(cols_cible[index]):
            if not (col_cible in cols_cible_filter):
                continue
            minute_col = cols_cible_minutes[index][index_cible]
            print(
                "--------------------------------------------------------------------------------"
            )
            print("///////////////////////////", col_cible, ">>", minute_col)
            y = df_limited[minute_col]            
            X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)
            # Réchantillonne
            # X_train_samp, y_train_samp = under_sampling(X_train, y_train)
            X_train_samp, y_train_samp = X_train, y_train

            # continue

            # Exécuter GridSearchCV pour chaque modèle
            for model_name, model in classifiers.items():
                # Controle run, car potentiellement long
                print("--------------------------------")
                print(f"GridSearchCV pour {model_name}")
                grid = GridSearchCV(
                    model,
                    param_grid[model_name],
                    scoring="f1_macro",
                    cv=crossval,
                    n_jobs=2,
                    verbose=2,
                )
                # Fit et Predict
                grid.fit(X_train_samp, y_train_samp)
                y_pred = grid.best_estimator_.predict(X_test)
                # y_pred = grid.predict(X_test)
                # Meilleur score et meilleurs hyperparamètres
                best_params = grid.best_params_
                best_score = grid.best_score_
                # affiche de suite les résultat
                print(f"Meilleurs paramètres {best_params}")
                print(f"Meilleur score {best_score}")
                # Accuracy
                accuracy = accuracy_score(y_test, y_pred)
                print(f"Accuracy : {accuracy}")
                # train et test score
                score_train = grid.score(X_train_samp, y_train_samp)
                print(f"Score train : {score_train}")
                score_test = grid.score(X_test, y_test)
                print(f"Score test : {score_test}")
                # Rapport détaillé
                detailled_report = classification_report(y_test, y_pred)
                print(f"Classification report :\n {detailled_report}")
                # Matrice de confusion
                ct = pd.crosstab(
                    y_test, y_pred, rownames=["Classe réelle"], colnames=["Classe prédite"]
                )
                display(ct)
                # Score de validation croisée
                #             scores = cross_validate(grid, X_train, y_train, cv=crossval, scoring=['accuracy', 'precision', 'recall', 'f1'])
                #             cv_test_accuracy = f" cv_test_accuracy : {scores['test_accuracy'].mean()} (+/-{scores['test_accuracy'].std()})"
                #             cv_test_precision
                #             cv_test_recall
                #             cv_test_f1

                # {'fit_time': array([1.7602632 , 1.3521595 , 1.53327417, 1.6628437 , 1.52980328]),
                #  'score_time': array([0.10070086, 0.10009599, 0.11566949, 0.09443331, 0.09455991]),
                #  'test_accuracy': array([0.87765306, 0.87768222, 0.8774344 , 0.87757839, 0.87759297]),
                #  'test_precision': array([0.36      , 0.43243243, 0.2745098 , 0.29032258, 0.38888889]),
                #  'test_recall': array([0.00107322, 0.00190794, 0.00166965, 0.00107335, 0.00250447]),
                #  'test_f1': array([0.00214005, 0.00379912, 0.00331911, 0.00213878, 0.00497689])}

                # print("[StackingClassifier]: \n Accuracy: %0.2f (+/- %0.2f)\n" % (scores['test_accuracy'].mean(), scores['test_accuracy'].std()),
                #       "F1 score: %0.2f (+/- %0.2f)" % (scores['test_f1'].mean(), scores['test_f1'].std()))
                # >>>
                # [StackingClassifier]:
                #  Accuracy: 0.76 (+/- 0.02)
                #  F1 score: 0.62 (+/- 0.04)

                # Ajouter au tableau des résultats
                results.append(
                    {
                        "Target": minute_col,
                        "Year floor": 2024 - 16 + year_floor,
                        "Model": model_name,
                        "Best Params": best_params,
                        "Best Score": best_score,
                        "Accuracy Test": accuracy,
                        "Score Train": score_train,
                        "Score Test": score_test,
                        "Detailled_report": detailled_report,
                        "Prédiction": ct,
                    }
                )
                df_results = pd.DataFrame(results)
                df_results = df_results.sort_values(by=["Target", "Score Test"], ascending=False)
                df_results.to_csv(f"../data/_GridSearch_classifier.csv", sep=";", index=False)

print(results)
df_results = pd.DataFrame(results)
df_results = df_results.sort_values(by=["Target", "Score Test"], ascending=False)
df_results.to_csv(f"../data/_GridSearch_classifier.csv", sep=";", index=False)

# p = plt.figure(figsize=(18,12))
# p = sns.set_theme(style="white")
# p = models=models.sort_values(by='Model Accuracy with GridSearch',ascending=False)
# p = sns.barplot(y= 'Model', x= 'Model Accuracy with GridSearch', data= models)
# for container in p.containers:
#     p.bar_label(container,label_type = 'edge',padding = 8,size = 20,color = "black",rotation = 0,
#     bbox={"boxstyle": "round", "pad": 0.6, "facecolor": "pink", "edgecolor": "Blue", "alpha": 1})
# plt.title('COMPARE THE MODEL')
# plt.xlabel('MODEL')
# plt.ylabel('Model Accuracy')
# plt.show()

-----------------------------------------------------
year 2021
-----------------------------------------------------
TurnoutTimeMinutes_min TurnoutTimeSeconds_min
cols_cible [['TurnoutTimeSeconds_min', 'TurnoutTimeSeconds_mean', 'TurnoutTimeSeconds_max'], ['TravelTimeSeconds_min', 'TravelTimeSeconds_mean', 'TravelTimeSeconds_max'], ['PumpSecondsOnSite_min', 'PumpSecondsOnSite_mean', 'PumpSecondsOnSite_max']]
cols_cible_minutes [['TurnoutTimeMinutes_min', 'TurnoutTimeMinutes_mean', 'TurnoutTimeMinutes_max'], ['TravelTimeMinutes_min', 'TravelTimeMinutes_mean', 'TravelTimeMinutes_max'], ['PumpMinutesOnSite_min', 'PumpMinutesOnSite_mean', 'PumpMinutesOnSite_max']]
TurnoutTimeMinutes_mean TurnoutTimeSeconds_mean
cols_cible [['TurnoutTimeSeconds_min', 'TurnoutTimeSeconds_mean', 'TurnoutTimeSeconds_max'], ['TravelTimeSeconds_min', 'TravelTimeSeconds_mean', 'TravelTimeSeconds_max'], ['PumpSecondsOnSite_min', 'PumpSecondsOnSite_mean', 'PumpSecondsOnSite_max']]
cols_cible_minutes [['TurnoutTime

CalYear  HourOfCall_0  HourOfCall_1  HourOfCall_2  HourOfCall_3  \
1147280       13             0             0             0             0   
1147281       13             0             0             0             0   
1147282       13             0             0             0             0   

         HourOfCall_4  PropertyType_0  PropertyType_1  PropertyType_2  \
1147280             1               0               0               0   
1147281             1               0               0               0   
1147282             1               0               0               0   

         PropertyType_3  PropertyType_4  PropertyType_5  PropertyType_6  \
1147280               1               0               1               0   
1147281               1               0               1               1   
1147282               0               0               0               0   

         PropertyType_7  PropertyType_8  Postcode_district_0  \
1147280               1               0                    0   
1147281               1               1                    0   
1147282               1               0                    0   

         Postcode_district_1  Postcode_district_2  Postcode_district_3  \
1147280                    0                    0                    0   
1147281                    0                    0                    0   
1147282                    0                    0                    0   

         Postcode_district_4  NumPumpsAttending  StopCode_0  StopCode_1  \
1147280                    1               1.00           0           0   
1147281                    1               1.00           0           0   
1147282                    1               1.00           0           0   

         StopCode_2  StopCode_3  StopCode_4  Month_0  Month_1  Month_2  \
1147280           0           1           1        0        0        0   
1147281           0           1           0        0        0        0   
1147282           0           1           1        0        0        0   

         Month_3  DayOfWeek_0  DayOfWeek_1  DayOfWeek_2  \
1147280        1            0            1            0   
1147281        1            0            1            0   
1147282        1            0            1            0   

         PumpSecondsOnSite_min  PumpSecondsOnSite_mean  PumpSecondsOnSite_max  \
1147280                2880.00                 2880.00                2880.00   
1147281                 420.00                  420.00                 420.00   
1147282                 600.00                  600.00                 600.00   

         TurnoutTimeSeconds_min  TurnoutTimeSeconds_mean  \
1147280                   48.00                    48.00   
1147281                  114.00                   114.00   
1147282                  131.00                   131.00   

         TurnoutTimeSeconds_max  TravelTimeSeconds_min  \
1147280                   48.00                 133.00   
1147281                  114.00                 136.00   
1147282                  131.00                 245.00   

         TravelTimeSeconds_mean  TravelTimeSeconds_max TurnoutTimeMinutes_min  \
1147280                  133.00                 133.00                  64.00   
1147281                  136.00                 136.00                1192.00   
1147282                  245.00                 245.00                1192.00   

        TurnoutTimeMinutes_mean TurnoutTimeMinutes_max  
1147280                   53.00                  57.00  
1147281                 1192.00                1192.00  
1147282                 1192.00                1192.00

(444247, 45)
cols_to_remove ['TurnoutTimeSeconds_min', 'TurnoutTimeSeconds_mean', 'TurnoutTimeSeconds_max', 'TravelTimeSeconds_min', 'TravelTimeSeconds_mean', 'TravelTimeSeconds_max', 'PumpSecondsOnSite_min', 'PumpSecondsOnSite_mean', 'PumpSecondsOnSite_max', 'TurnoutTimeMinutes_min', 'TurnoutTimeMinutes_mean', 'TurnoutTimeMinutes_max', 'NumPumpsAttending']
cols_to_keep ['CalYear', 'HourOfCall_0', 'HourOfCall_1', 'HourOfCall_2', 'HourOfCall_3', 'HourOfCall_4', 'Postcode_district_0', 'Postcode_district_1', 'Postcode_district_2', 'Postcode_district_3', 'Postcode_district_4', 'Month_0', 'Month_1', 'Month_2', 'Month_3', 'DayOfWeek_0', 'DayOfWeek_1', 'DayOfWeek_2']


CalYear  HourOfCall_0  HourOfCall_1  HourOfCall_2  HourOfCall_3  \
1147280       13             0             0             0             0   
1147281       13             0             0             0             0   

         HourOfCall_4  Postcode_district_0  Postcode_district_1  \
1147280             1                    0                    0   
1147281             1                    0                    0   

         Postcode_district_2  Postcode_district_3  Postcode_district_4  \
1147280                    0                    0                    1   
1147281                    0                    0                    1   

         Month_0  Month_1  Month_2  Month_3  DayOfWeek_0  DayOfWeek_1  \
1147280        0        0        0        1            0            1   
1147281        0        0        0        1            0            1   

         DayOfWeek_2  
1147280            0  
1147281            0

(444247, 18)
--------------------------------------------------------------------------------
/////////////////////////// TurnoutTimeSeconds_min >> TurnoutTimeMinutes_min
--------------------------------
GridSearchCV pour DecisionTreeClassifier
Fitting 5 folds for each of 36 candidates, totalling 180 fits
Meilleurs paramètres {'criterion': 'gini', 'max_depth': None, 'min_samples_split': 2}
Meilleur score 0.3582659531951722
Accuracy : 0.3733258300506472
Score train : 0.4000146791276352
Score test : 0.36305971565435957
Classification report :
               precision    recall  f1-score   support

        44.0       0.35      0.49      0.40     22490
        64.0       0.32      0.38      0.35     23234
        83.0       0.27      0.14      0.18     21135
      1192.0       0.57      0.47      0.51     21991

    accuracy                           0.37     88850
   macro avg       0.38      0.37      0.36     88850
weighted avg       0.38      0.37      0.36     88850



...

Classe prédite  44.00    64.00    84.00    1192.00
Classe réelle                                     
44.00              8166     5753     2493     1086
64.00              6423     6321     3045     1598
84.00              5288     5366     2941     3382
1192.00            3575     3062     2075     7953

--------------------------------
GridSearchCV pour RandomForestClassifier
Fitting 5 folds for each of 32 candidates, totalling 160 fits
Meilleurs paramètres {'criterion': 'gini', 'max_depth': 10, 'n_estimators': 50}
Meilleur score 0.3645653940549374
Accuracy : 0.38357143899484875
Score train : 0.37631266018805326
Score test : 0.36500914207383695
Classification report :
               precision    recall  f1-score   support

        44.0       0.36      0.48      0.41     17498
        64.0       0.32      0.48      0.38     17387
        84.0       0.30      0.09      0.14     16977
      1192.0       0.58      0.48      0.53     16665

    accuracy                           0.38     68527
   macro avg       0.39      0.38      0.37     68527
weighted avg       0.39      0.38      0.36     68527



Classe prédite  44.00    64.00    84.00    1192.00
Classe réelle                                     
44.00              8345     7147     1073      933
64.00              6196     8321     1408     1462
84.00              5038     7028     1547     3364
1192.00            3544     3890     1159     8072

--------------------------------
GridSearchCV pour MLPClassifier
Fitting 5 folds for each of 36 candidates, totalling 180 fits


KeyboardInterrupt: 

In [ ]:
# Assurez-vous que 'Score Test' est numérique
df_results["Score Test"] = pd.to_numeric(df_results["Score Test"], errors="coerce")

# Créez une liste des valeurs uniques de 'Target'
targets = df_results["Target"].unique()

# Boucle sur chaque 'Target' pour créer des graphiques séparés
for target in targets:
    # Filtrer les données pour cette Target
    df_target = df_results[df_results["Target"] == target]

    # Trier par 'Score Test' et prendre les 3 premiers
    top_3_models = df_target.nlargest(3, "Score Test")

    # Créer le graphique à barres
    plt.figure(figsize=(10, 6))
    plt.bar(top_3_models["Model"], top_3_models["Score Test"], color="skyblue")

    # Ajouter des titres et labels
    plt.title(f"Top 3 Models for Target: {target}", fontsize=14)
    plt.xlabel("Model", fontsize=12)
    plt.ylabel("Score Test", fontsize=12)
    plt.xticks(rotation=45, ha="right")

    # Enregistrer l'image
    plt.tight_layout()  # Assure que le contenu ne dépasse pas du graphique
    plt.show()
    # plt.savefig(f"top_3_models_{target}.png")
    plt.close()  # Fermer la figure après l'enregistrement

In [ ]:




grid.best_estimator_ Classifier
Stacking Classifier

	# Define base classifiers
clf1 = LogisticRegression(random_state=42)
clf2 = DecisionTreeClassifier(random_state=42)
clf3 = SVC(probability=True, random_state=42)
	# Define VotingClassifier
voting_clf = VotingClassifier(estimators=[('lr', clf1), ('dt', clf2), ('svc', clf3)], voting='soft')
	# Define parameter grid
param_grid = {
    'lr__C': [0.1, 1, 10],
    'dt__max_depth': [3, 5, 7],
    'svc__C': [0.1, 1, 10],
    'voting': ['hard', 'soft']
}
	# Perform grid search
grid_search = GridSearchCV(estimator=voting_clf,
                           param_grid=param_grid,
                           cv=5,
                           scoring='accuracy')
grid_search.fit(X_train, y_train)
	# Report best score and parameters
print(f"Best score: {grid_search.best_score_:.3f}")
print(f"Best parameters: {grid_search.best_params_}")
	# Evaluate on test set
best_model = grid_search.best_estimator_
accuracy = best_model.score(X_test, y_test)
print(f"Test set accuracy: {accuracy:.3f}")


XGBoost 
LCEClassifier

from sklearn.ensemble import RandomForestClassifier,ExtraTreesClassifier
from sklearn.svm import SVC
from sklearn.neural_network import MLPClassifier

rnd_clf = RandomForestClassifier(n_estimators=100,random_state=42)
extra_trees_clf = ExtraTreesClassifier(n_estimators=100,random_state=42)
svm_clf = SVC(max_iter=100,tol=20,random_state=42)
mlp_clf = MLPClassifier(random_state=42)

estimators = [rnd_clf,extra_trees_clf,svm_clf,mlp_clf]
for estimator in estimators:
    print("Training the", estimator)
    estimator.fit(X_train,y_train)
    
from sklearn.ensemble import VotingClassifier

named_estimators = [
    ("random_forest_clf",rnd_clf),
    ("Extra_trees_clf",extra_trees_clf),
    ("SVM",svm_clf),
    ("MLP",mlp_clf)
]

voting_clf = VotingClassifier(named_estimators)

print(voting_clf.fit(X_train,y_train))
print("voting_clf.score:",voting_clf.score(X_test,y_test))